In [1]:
import pandas as pd 
import numpy as np 
from sklearn.impute import SimpleImputer, KNNImputer
from sklearn.preprocessing import StandardScaler
from sklearn.experimental import enable_iterative_imputer  # noqa
# now you can import normally from sklearn.impute
from sklearn.impute import IterativeImputer
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import confusion_matrix, classification_report
import matplotlib.pyplot as plt
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import plot_confusion_matrix, make_scorer
from sklearn.metrics import accuracy_score, f1_score, roc_curve, auc, roc_auc_score
from sklearn.model_selection import RepeatedKFold, KFold, cross_val_score, StratifiedKFold
import xgboost
import xgboost as xgb
from xgboost import XGBClassifier
from sklearn.utils import class_weight
from sklearn.utils.class_weight import compute_sample_weight
from sklearn.pipeline import Pipeline

In [2]:
# LEER LOS DATOS 
file_in = pd.read_csv('prediction_of_AHE.csv') #lee archivo 
file_in = file_in.drop(['subject_id', 'hadm_id', 'icustay_id'], axis= 'columns') #elimino las columnas que no ocupo 
file_in = file_in.sample(frac=1) #hago una mezcla de manera aleatoria en el dataframe
# IMPUTACIÓN DE DATOS 
x = file_in.drop(['AHE'], axis='columns') #para mis variables de entrada soalamente elimino la varaible a predecir
y= file_in.AHE #me quedo con la variable a predecir en y 
columnas= x.columns 


# DIVIDIR CONJUNTO DE ENTRENAMIENTO, VALIDACIÓN Y PRUEBA 
x_train, x_test, y_train, y_test = train_test_split( x, y, test_size=0.3, )
print('X_train:', x_train.shape, 'X_test:', x_test.shape) 

#data = x.replace(" ", np.NaN)
#values = data.values
imp = IterativeImputer(max_iter=40).fit(x_train) 
#imp = KNNImputer(n_neighbors=5, weights= 'uniform').fit(x_train)
##imp = MissForest()

#imp= SimpleImputer(missing_values=np.nan, strategy='median').fit(x_train) #mean, most frequent, constant 
x_train = imp.fit_transform(x_train)
x_test = imp.fit_transform(x_test)
print('X_train:', x_train.shape, 'X_test:', x_test.shape)


X_train: (14943, 40) X_test: (6405, 40)
X_train: (14943, 40) X_test: (6405, 40)


In [3]:
print(type(x_train))
x_train_imputado = pd.DataFrame(x_train, columns=[columnas]) #convirtiendo el arreglo en dataframe 
x_test_imputado = pd.DataFrame(x_test, columns=[columnas])
x_train_imputado

<class 'numpy.ndarray'>


heartrate_min heartrate_mean heartrate_max sysbp_min  sysbp_mean  \
0              73.0     104.511415         152.0      70.0  103.462617   
1              42.0      51.791667          78.0      85.0  117.000000   
2              53.0      92.725490         143.0      60.0  119.753138   
3              68.0      85.136054         101.0      86.0  140.103704   
4              67.0      82.017857         104.0      79.0  105.013514   
...             ...            ...           ...       ...         ...   
14938          60.0      76.108280          97.0       2.0  119.087432   
14939          65.0      84.510204         100.0      86.0  117.500000   
14940          47.0      73.914384         138.0      76.0  124.199313   
14941          54.0      70.488889          88.0      96.0  125.085106   
14942          30.0      93.283816         150.0      54.0  113.812431   

      sysbp_max diasbp_min diasbp_mean diasbp_max meanbp_min  ... first_tsicu  \
0         159.0       30.0   52.957944      101.0       42.0  ...         0.0   
1         137.0       49.0   60.000000       69.0       60.0  ...         0.0   
2         181.0       25.0   64.987500       98.0       28.0  ...         0.0   
3         172.0       22.0   80.318519      140.0       33.0  ...         0.0   
4         132.0       42.0   59.743243       96.0       53.0  ...         0.0   
...         ...        ...         ...        ...        ...  ...         ...   
14938     155.0       45.0   60.390110      123.0       56.0  ...         0.0   
14939     202.0       37.0   59.140000       91.0       12.0  ...         0.0   
14940     195.0       37.0   74.865979      134.0       50.0  ...         0.0   
14941     155.0       39.0   52.712766      139.0       60.0  ...         1.0   
14942     169.0       15.0   61.082314      109.0       39.0  ...         0.0   

      first_csru first_nicu last_sicu last_micu last_ccu last_tsicu last_csru  \
0            0.0        0.0       0.0       1.0      0.0        0.0       0.0   
1            0.0        0.0       0.0       1.0      0.0        0.0       0.0   
2            0.0        0.0       0.0       1.0      0.0        0.0       0.0   
3            0.0        0.0       0.0       1.0      0.0        0.0       0.0   
4            1.0        0.0       0.0       0.0      0.0        0.0       1.0   
...          ...        ...       ...       ...      ...        ...       ...   
14938        0.0        0.0       1.0       0.0      0.0        0.0       0.0   
14939        0.0        0.0       1.0       0.0      0.0        0.0       0.0   
14940        0.0        0.0       0.0       1.0      0.0        0.0       0.0   
14941        0.0        0.0       0.0       0.0      0.0        1.0       0.0   
14942        0.0        0.0       0.0       0.0      0.0        0.0       1.0   

      last_nicu          kg  
0           0.0   61.000000  
1           0.0   73.000000  
2           0.0   63.200000  
3           0.0   92.000000  
4           0.0  128.300000  
...         ...         ...  
14938       0.0   84.800003  
14939       0.0  161.300000  
14940       0.0   39.799999  
14941       0.0   96.800000  
14942       0.0   45.400002  

[14943 rows x 40 columns]

In [4]:
# ESTANDARIZACIÓN DE DATOS 
estandarizar = ['age', 'kg', 'creatinine','heartrate_min', 'heartrate_mean', 'heartrate_max', 'sysbp_min',
       'sysbp_mean', 'sysbp_max', 'diasbp_min', 'diasbp_mean', 'diasbp_max',
       'meanbp_min', 'meanbp_mean', 'meanbp_max', 'resprate_min','resprate_mean', 'resprate_max', 'tempc_min', 'tempc_mean', 'tempc_max',
       'spo2_min', 'spo2_mean', 'spo2_max', 'pao2_min', 'pao2_mean','pao2_max']
dummies = ['sexo', 'first_sicu', 'first_micu',
       'first_ccu', 'first_tsicu', 'first_csru', 'first_nicu', 'last_sicu','last_micu', 'last_ccu', 'last_tsicu', 'last_csru', 'last_nicu']

#Intentar con las varaibles separadas y también juntas 
scaler = StandardScaler().fit(x_train_imputado)
#transformed_values[estandarizar] = scaler.fit_transform(transformed_values[estandarizar]) #estandarizo las variables númericas 
x_train_escalado = scaler.fit_transform(x_train_imputado)
x_test_escalado = scaler.fit_transform(x_test_imputado)

#COLOCAR PRINTS 
print('X_train:', x_train_escalado.shape, 'X_test:', x_test_escalado.shape)

X_train: (14943, 40) X_test: (6405, 40)


In [5]:
# DEFINIR MODELO A UTILIZAR 
#RF
modeloXGB = xgb.XGBClassifier(use_label_encoder=False)
modeloRF = RandomForestClassifier()
#DEFINIR PARÁMETROS A ITERAR

parametrosRF = {'n_estimators': range(10, 200, 10), 'criterion':['gini', 'entropy'], 'max_depth': range(1,10,1), 
              'max_features':['auto', 'sqrt', 'log2'],  'min_impurity_decrease':[1e-4, 1e-7], 
              'class_weight':['balanced', 'balanced_subsample']} # PARA RF
 # PARA RF

parametrosRFprueba = {'n_estimators': range(10, 200, 10),'max_depth': range(1,10,1),'class_weight':['balanced']}

ratio = float(np.sum(y_train == 0)) / np.sum(y_train==1)
                      
parametrosXGB = {'loss':['deviance', 'exponential'], 'criterion':['friedman_mse', 'mse', 'mae'], 'max_features':['auto', 'sqrt',
              'log2'], 'n_estimators': range(10, 200, 10), "learning_rate": [0.1,0.05],"colsample_bytree" : [0.4, 0.8],
                    "subsample" : [0.8, 0.4], "reg_alpha" : [0.5], "reg_lambda": [2],
                    "objective": ['binary:logistic'],  'max_depth': range(1,10,1), "gamma":[10],"rate_drop": [0.5, 0.3],
                    "seed": [422], "eval_metric": ['auc'],"scale_pos_weight": [ratio]}

parametrosXGBprueba = { 'n_estimators': range(10, 200, 10), "learning_rate": [0.1,0.05], 'max_depth': range(1,10,1),
                        "eval_metric": ['auc'],"scale_pos_weight": [ratio]}

# Probar entre balanaear y  no balancear 

#ENTRENAR GRID SEARCH 
balanced = class_weight.compute_sample_weight('balanced', y_train)
RKF = RepeatedKFold(n_splits=5, n_repeats=2, random_state=422) #probar los CROSS VALIDATION
SKF = StratifiedKFold(n_splits=5, shuffle= True, random_state=422)
grid = GridSearchCV(estimator= modeloRF, param_grid= parametrosRF, cv=RKF, scoring='roc_auc', verbose=2, refit= True)


In [6]:
grid.fit(x_train, y_train, sample_weight = balanced)

Fitting 10 folds for each of 4104 candidates, totalling 41040 fits
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=10; total time=   0.0s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=10; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=10; total time=   0.0s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=10; total time=   0.0s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=10; total time=   0.0s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=10; total time=   0.0s
[CV] END class_weight=balanced, criterion=gini, max_depth

[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=60; total time=   0.2s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=60; total time=   0.2s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=60; total time=   0.2s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=60; total time=   0.3s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=70; total time=   0.3s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=70; total time=   0.3s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=7

[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=120; total time=   0.5s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=120; total time=   0.6s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=120; total time=   0.5s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=120; total time=   0.5s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=120; total time=   0.5s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=120; total time=   0.5s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estima

[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=170; total time=   0.7s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=170; total time=   0.7s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=180; total time=   0.7s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=180; total time=   0.8s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=180; total time=   0.8s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estimators=180; total time=   0.7s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=0.0001, n_estima

[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=40; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=40; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=40; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=40; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=40; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=50; total time=   0.1s
[CV] END class_weight=balanced, criterion=gini, max_depth=1, max_features=auto, min_impurity_decrease=1e-07, n_estimators=50; tota

...

[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=0.0001, n_estimators=190; total time=   3.8s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=0.0001, n_estimators=190; total time=   3.8s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=0.0001, n_estimators=190; total time=   3.8s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=0.0001, n_estimators=190; total time=   3.8s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=0.0001, n_estimators=190; total time=   3.8s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=10; total time=   0.1s
[CV] END class_weight=balanced_subsample, 

[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=50; total time=   0.9s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=50; total time=   0.9s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=50; total time=   0.9s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=60; total time=   1.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=60; total time=   1.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=60; total time=   1.1s
[CV] END class_weight=balanced_subsample, criterion=

[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=100; total time=   1.9s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=110; total time=   2.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=110; total time=   2.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=110; total time=   2.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=110; total time=   2.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=110; total time=   2.1s
[CV] END class_weight=balanced_subsample, crit

[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=160; total time=   3.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=160; total time=   3.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=160; total time=   3.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=160; total time=   3.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=160; total time=   3.1s
[CV] END class_weight=balanced_subsample, criterion=entropy, max_depth=9, max_features=log2, min_impurity_decrease=1e-07, n_estimators=160; total time=   3.1s
[CV] END class_weight=balanced_subsample, crit

GridSearchCV(cv=RepeatedKFold(n_repeats=2, n_splits=5, random_state=422),
             estimator=RandomForestClassifier(),
             param_grid={'class_weight': ['balanced', 'balanced_subsample'],
                         'criterion': ['gini', 'entropy'],
                         'max_depth': range(1, 10),
                         'max_features': ['auto', 'sqrt', 'log2'],
                         'min_impurity_decrease': [0.0001, 1e-07],
                         'n_estimators': range(10, 200, 10)},
             scoring='roc_auc', verbose=2)

In [7]:
# METRICAS DEL MODELO 
auc_train = grid.best_score_
std_train = grid.cv_results_['std_test_score'][grid.best_index_]
best_params = grid.best_params_
best_estimator = grid.best_estimator_

print("auc:",auc_train)
print("std_validation:",std_train)
print('best estimator:', best_estimator)
print('best parameters:',best_params)

auc: 0.8273495061368366
std_validation: 0.008441600723984075
best estimator: RandomForestClassifier(class_weight='balanced', criterion='entropy',
                       max_depth=8, min_impurity_decrease=0.0001,
                       n_estimators=160)
best parameters: {'class_weight': 'balanced', 'criterion': 'entropy', 'max_depth': 8, 'max_features': 'auto', 'min_impurity_decrease': 0.0001, 'n_estimators': 160}
